Word Embeddings

1. average the vector for each single word in ImageNet list

In [1]:
from gensim.models import Word2Vec
from gensim.test.utils import common_texts
from gensim.models import Word2Vec
import gensim.downloader as api
import gensim

import pandas as pd
import numpy as np



In [2]:
#As model we use a pretrained model from FastText:
# https://fasttext.cc/docs/en/pretrained-vectors.html
# This model has 6gb of data DISCUSSION: Should we use it?
model = gensim.models.KeyedVectors.load_word2vec_format('./wiki.enc.vectors', binary=False)

In [3]:
#word2vec_model’ parameter is the loaded word2vec model
#‘words’ parameter is a tokens list (strings) of the sentence / paragraph / document that you want to calculate
def get_mean_vector(word2vec_model, words):
    # remove out-of-vocabulary words
    words = [word for word in words if word in word2vec_model.key_to_index]
    if len(words) >= 1:
        return np.mean(word2vec_model[words], axis=0)
    else:
        return []

In [4]:
df_imgnet = pd.read_csv("../files/ImageNet.csv")
class_list = df_imgnet["Class Name"].tolist()

In [5]:
averaged_vectors = []
for el in class_list:
    vec = get_mean_vector(model, el)
    if len(vec) > 0:
      # do somthing with the vector ${vec}
      averaged_vectors.append(vec)

In [6]:
#TODO: Check if this is correct and how to find zero vectors.
averaged_vectors

[array([ 5.83745725e-02,  1.11299288e-02, -8.53278767e-03,  6.00575022e-02,
        -6.14714110e-03,  1.54958650e-01,  1.99728669e-03, -6.84639290e-02,
        -2.39511412e-02,  6.44611493e-02,  6.14283606e-02,  1.18290223e-01,
        -3.71867828e-02,  8.36375132e-02, -2.43158545e-02, -8.14421400e-02,
        -8.75932053e-02,  3.45799862e-03,  2.96249278e-02,  3.74225713e-02,
         8.51560086e-02, -3.53916436e-02, -3.87921510e-03,  1.28354998e-02,
         1.55907229e-03, -4.24466431e-02,  1.32647365e-01,  7.98933506e-02,
         6.11335551e-03,  4.61054221e-02,  3.39957140e-02,  1.11466773e-01,
         5.21178581e-02, -7.38002807e-02, -2.76981425e-02,  1.15924649e-01,
        -7.31871277e-02,  7.88921304e-03, -1.33104295e-01, -3.80728533e-03,
         1.30262878e-02,  5.72185703e-02, -6.85079321e-02, -6.81604967e-02,
         6.06365018e-02,  3.11642122e-02,  5.35399914e-02, -3.50985932e-03,
         6.04485758e-02,  1.15064988e-02,  1.32491067e-01,  1.37778476e-03,
        -5.7

2. take zero vectors for words can not be vectorized. for example for hammerhead shark, hammerhead could be zero, but still /2 because two words

In [ ]:
#TODO:

First Approach:
Take each item in the ImageNet list, prepare to each dbpedia Class and take the highest score

In [7]:
img_net = pd.read_csv("../files/ImageNet.csv")
img_net_list = img_net["Class Name"].tolist()

dbpedia = pd.read_csv("../files/dbpedia_classes.csv")
db_list = dbpedia["label"].tolist()


In [8]:
sim_df = pd.DataFrame(index =db_list ,columns =img_net_list)


In [9]:
for el_img in img_net_list:
    for el_db in db_list:
        if len(el_img) == 1:
            try:
                sim = model.similarity(el_img,el_db)
                sim_df.at[el_db,el_img] = sim
            except:
                sim_df.at[el_db,el_img] = "Not present"
        elif len(el_img) > 1:
            for el_array in el_img:  #we choose the entry with the highest value
                val = 0
                try:
                    sim = model.similarity(el_img,el_db)
                    if sim > val:
                        sim_df.at[el_db,el_img] = sim
                except:
                    sim_df.at[el_db,el_img] = "Not present"

In [36]:
sim_df

tench, Tinca tinca goldfish, Carassius auratus  \
company           Not present                 Not present   
activity          Not present                 Not present   
name              Not present                 Not present   
person            Not present                 Not present   
actor             Not present                 Not present   
...                       ...                         ...   
Wind motor        Not present                 Not present   
Windmill          Not present                 Not present   
wine              Not present                 Not present   
woman             Not present                 Not present   
zoo               Not present                 Not present   

           great white shark, white shark, man-eater, man-eating shark, Carcharodon caharias',  \
company                                           Not present                                    
activity                                          Not present                                    
name                                              Not present                                    
person                                            Not present                                    
actor                                             Not present                                    
...                                                       ...                                    
Wind motor                                        Not present                                    
Windmill                                          Not present                                    
wine                                              Not present                                    
woman                                             Not present                                    
zoo                                               Not present                                    

           tiger shark, Galeocerdo cuvieri hammerhead, hammerhead shark  \
company                        Not present                  Not present   
activity                       Not present                  Not present   
name                           Not present                  Not present   
person                         Not present                  Not present   
actor                          Not present                  Not present   
...                                    ...                          ...   
Wind motor                     Not present                  Not present   
Windmill                       Not present                  Not present   
wine                           Not present                  Not present   
woman                          Not present                  Not present   
zoo                            Not present                  Not present   

           electric ray, crampfish, numbfish, torpedo     stingray  \
company                                   Not present     0.027284   
activity                                  Not present     0.012846   
name                                      Not present     0.046808   
person                                    Not present     0.071456   
actor                                     Not present     0.043854   
...                                               ...          ...   
Wind motor                                Not present  Not present   
Windmill                                  Not present  Not present   
wine                                      Not present     0.029963   
woman                                     Not present     0.103416   
zoo                                       Not present     0.119585   

                   cock          hen ostrich, Struthio camelus  ...  \
company        0.041822     0.005975               Not present  ...   
activity       0.061037     0.007359               Not present  ...   
name           0.086031     0.002293               Not present  ...   
person         0.088371     0.099589               Not present  ...   
acto

In [62]:
#replace all Not present with NaN
sim_df =sim_df.replace(-2, np.nan) #I tried it with -2 before but nan is better way to go
sim_df

tench, Tinca tinca  goldfish, Carassius auratus  \
company                    NaN                          NaN   
activity                   NaN                          NaN   
name                       NaN                          NaN   
person                     NaN                          NaN   
actor                      NaN                          NaN   
...                        ...                          ...   
Wind motor                 NaN                          NaN   
Windmill                   NaN                          NaN   
wine                       NaN                          NaN   
woman                      NaN                          NaN   
zoo                        NaN                          NaN   

            great white shark, white shark, man-eater, man-eating shark, Carcharodon caharias',  \
company                                                   NaN                                     
activity                                                  NaN                                     
name                                                      NaN                                     
person                                                    NaN                                     
actor                                                     NaN                                     
...                                                       ...                                     
Wind motor                                                NaN                                     
Windmill                                                  NaN                                     
wine                                                      NaN                                     
woman                                                     NaN                                     
zoo                                                       NaN                                     

            tiger shark, Galeocerdo cuvieri  hammerhead, hammerhead shark  \
company                                 NaN                           NaN   
activity                                NaN                           NaN   
name                                    NaN                           NaN   
person                                  NaN                           NaN   
actor                                   NaN                           NaN   
...                                     ...                           ...   
Wind motor                              NaN                           NaN   
Windmill                                NaN                           NaN   
wine                                    NaN                           NaN   
woman                                   NaN                           NaN   
zoo                                     NaN                           NaN   

            electric ray, crampfish, numbfish, torpedo  stingray      cock  \
company                                            NaN  0.027284  0.041822   
activity                                           NaN  0.012846  0.061037   
name                                               NaN  0.046808  0.086031   
person                                             NaN  0.071456  0.088371   
actor                                              NaN  0.043854  0.035153   
...                                                ...       ...       ...   
Wind motor                                         NaN       NaN       NaN   
Windmill                                           NaN       NaN       NaN   
wine                                               NaN  0.029963  0.112761   
woman                                              NaN  0.103416  0.071672   
zoo                                                NaN  0.119585  0.077206   

                 hen  ostrich, Struthio camelus  ...  \
company     0.005975                        NaN  ...   
activity    0.007359                        NaN  ...   
name        0.002293                

Now we get the highest value of each column and index and drop all values that are not available.

In [123]:
df = sim_df
max_df = df.idxmax()
cleaned_max_df = max_df.dropna()
max_val = pd.DataFrame(cleaned_max_df, columns=["Dbpedia"])


In [124]:
#this gives us all values of imagenet classes that are available
max_val_list = []
for el in cleaned_max_df.index:
    max_val_list.append(df[el].max())
max_val["Similarity"] = max_val_list

In [125]:
max_val = max_val.sort_values(by='Similarity', ascending=False)
max_val.index.name = "ImageNet"
max_val.head(100)

Dbpedia  Similarity
ImageNet                              
boxer                boxer    1.000000
library            library    1.000000
castle              castle    1.000000
monastery        monastery    1.000000
mosque              mosque    1.000000
volcano            volcano    1.000000
banjo               guitar    0.706532
obelisk           monument    0.678527
moped           motorcycle    0.664459
viaduct             bridge    0.661180
trombone            guitar    0.635482
cricket          cricketer    0.622020
cup             tournament    0.601954
missile             rocket    0.594302
ambulance         hospital    0.593846
mushroom            fungus    0.591072
menu            restaurant    0.571009
minibus              train    0.563798
airliner          aircraft    0.558762
guacamole           cheese    0.548568
admiral         lieutenant    0.548130
throne               reign    0.542236
lionfish              fish    0.540183
agaric              fungus    0.537672
schooner              ship    0.529205
bolete              fungus    0.526900
eel                   fish    0.525415
rifle               weapon    0.519779
tripod              camera    0.518418
pomegranate          grape    0.518394
volleyball       athletics    0.515404
projector           camera    0.513396
baseball         athletics    0.510783
pier                 beach    0.509402
palace              castle    0.508104
altar               church    0.498495
umbrella      organisation    0.497886
cheeseburger        cheese    0.497411
basketball       athletics    0.492495
hamster                cat    0.484335
bee                 insect    0.482826
jellyfish           insect    0.482466
fountain          monument    0.481206
dough               cheese    0.477563
dome                 tower    0.477254
snowmobile      motorcycle    0.475090
radiator            engine    0.472871
strawberry           grape    0.472666
pretzel             cheese    0.472052
chain           restaurant    0.470392
ski                  skier    0.469936
hummingbird           bird    0.469037
isopod          crustacean    0.468652
triceratops        reptile    0.467321
cassette             album    0.466115
harp                guitar    0.463781
tractor           aircraft    0.461083
weevil              fungus    0.458852
espresso             vodka    0.456520
ox                   horse    0.451102
tarantula          reptile    0.443726
bassoon             guitar    0.443350
lifeboat        lighthouse    0.441273
stretcher         hospital    0.439358
padlock               lock    0.439326
sundial           monument    0.438546
trilobite       crustacean    0.436651
mortar              rocket    0.436226
geyser             volcano    0.432103
pole                  race    0.429789
burrito             cheese    0.428803
holster             weapon    0.427635
stage              theatre    0.426994
turnstile        escalator    0.426139
planetarium         museum    0.423728
magpie                bird    0.421461
cauliflower         cheese    0.421422
eggnog               vodka    0.421245
collie                 dog    0.418997
banana              cheese    0.418558
beagle                 dog    0.414453
wing              aircraft    0.412505
carbonara           cheese    0.409837
centipede         arachnid    0.408475
modem               device    0.407938
wombat                 dog    0.405942
lemon               cheese    0.405616
cannon              weapon    0.403919
scorpion        crustacean    0.403289
speedboat       motorcycle    0.402685
tick                insect    0.398219
minivan         motorcycle    0.396956
gondola          escalator    0.395537
malinois               dog    0.394786
printer             device    0.394748
lotion               vodka    0.394414
barbershop         musical    0.394196
armadillo          reptile    0.393530
barn              building    0.392630
rapeseed             grape    0.392600

Second Approach: Average the vector of the items in imageNet class.
In the End we gotTwo sets of results. 
Write a function for top three matchings of dbpedia_class

In [ ]:
#TODO: